In [72]:
import pandas as pd
import technical.indicators as ftt
from functools import reduce
from datetime import datetime, timedelta
import numpy as np
import plotly.graph_objects as go

In [2]:
buy_params = {
        "buy_trend_above_senkou_level": 1,
        "buy_trend_bullish_level": 6,
        "buy_fan_magnitude_shift_value": 3,
        "buy_min_fan_magnitude_gain": 1.002 # NOTE: Good value (Win% ~70%), alot of trades
        #"buy_min_fan_magnitude_gain": 1.008 # NOTE: Very save value (Win% ~90%), only the biggest moves 1.008,
    }

In [3]:
sell_params = {
        "sell_trend_indicator": "trend_close_2h",
    }

# Import data for ADA/USDT

In [5]:
import re
import os

In [12]:
files = os.listdir("./data_research")

In [16]:
ada_usdt_files = [file_name for file_name in os.listdir("./data_research") if bool(re.match("ADAUSDT", file_name))]

In [17]:
ada_usdt_files

['ADAUSDT-5m-2023-11.csv', 'ADAUSDT-5m-2023-10.csv', 'ADAUSDT-5m-2023-09.csv']

In [51]:
ada_usdt = []
for file in ada_usdt_files:
    df = pd.read_csv(
        f"./data_research/{file}",
        names=[
            'open_time',
            'open',
            'high',
            'low',
            'close',
            'volume',
            'close_time',
            'quote_volume',
            'count',
            'taker_buy_volume',
            'taker_buy_quote_volume',
            'ignore'
        ]
    )
    ada_usdt.append(df)
    
ada_usdt = pd.concat(ada_usdt, axis=0, ignore_index=True)

In [52]:
ada_usdt.head()

open_time    open    high     low   close    volume     close_time  \
0  1698796800000  0.2929  0.2933  0.2921  0.2924  333226.1  1698797099999   
1  1698797100000  0.2923  0.2931  0.2921  0.2925  172703.4  1698797399999   
2  1698797400000  0.2925  0.2925  0.2920  0.2925  149870.5  1698797699999   
3  1698797700000  0.2926  0.2937  0.2924  0.2936  375250.7  1698797999999   
4  1698798000000  0.2936  0.2937  0.2924  0.2928  182167.5  1698798299999   

   quote_volume  count  taker_buy_volume  taker_buy_quote_volume  ignore  
0   97505.06580    388          231333.8             67685.92551       0  
1   50528.30234    209           67063.9             19619.82158       0  
2   43802.72365    187           66650.4             19482.90460       0  
3  110050.32249    379          186841.1             54796.96159       0  
4   53392.88143    295           93277.2             27333.59268       0

In [53]:
ada_usdt.drop(['open_time', 'quote_volume', 'count', 'taker_buy_volume', 'taker_buy_quote_volume', 'ignore'], axis=1, inplace=True)

In [54]:
ada_usdt.rename(columns={'close_time': 'datetime'}, inplace=True)

In [55]:
ada_usdt.sort_values(by='datetime', inplace=True)

In [56]:
ada_usdt.set_index('datetime', inplace=True)

In [57]:
ada_usdt.index = pd.to_datetime(ada_usdt.index, unit='ms')

## Final file

In [60]:
ada_usdt.head()

open    high     low   close     volume
datetime                                                          
2023-09-01 00:04:59.999  0.2554  0.2556  0.2550  0.2554   847128.5
2023-09-01 00:09:59.999  0.2555  0.2556  0.2553  0.2555   362375.9
2023-09-01 00:14:59.999  0.2555  0.2556  0.2555  0.2556   176382.6
2023-09-01 00:19:59.999  0.2556  0.2581  0.2556  0.2570  5336822.6
2023-09-01 00:24:59.999  0.2570  0.2572  0.2564  0.2565   333397.7

# Populate Indicators

In [63]:
def heikin_ashi(df):
    heikin_ashi_df = pd.DataFrame(index=df.index.values, columns=['open', 'high', 'low', 'close'])
    
    heikin_ashi_df['close'] = (df['open'] + df['high'] + df['low'] + df['close']) / 4
    
    for i in range(len(df)):
        if i == 0:
            heikin_ashi_df.iat[0, 0] = df['open'].iloc[0]
        else:
            heikin_ashi_df.iat[i, 0] = (heikin_ashi_df.iat[i-1, 0] + heikin_ashi_df.iat[i-1, 3]) / 2
        
    heikin_ashi_df['high'] = heikin_ashi_df.loc[:, ['open', 'close']].join(df['high']).max(axis=1)
    
    heikin_ashi_df['low'] = heikin_ashi_df.loc[:, ['open', 'close']].join(df['low']).min(axis=1)
    
    return heikin_ashi_df

In [64]:
# heikin ashi dataset
heikinashi = heikin_ashi(ada_usdt)

In [66]:
import talib.abstract as ta

In [73]:
def populate_indicators(dataframe):

    heikinashi = heikin_ashi(dataframe)
    dataframe['open'] = heikinashi['open']
    dataframe['close'] = heikinashi['close']
    dataframe['high'] = heikinashi['high']
    dataframe['low'] = heikinashi['low']
    
    # Close trend: EMA3, 6, 12, 24, 48, 72, 96
    dataframe['trend_close_5m'] = dataframe['close']
    dataframe['trend_close_15m'] = ta.EMA(dataframe['close'], timeperiod=3)
    dataframe['trend_close_30m'] = ta.EMA(dataframe['close'], timeperiod=6)
    dataframe['trend_close_1h'] = ta.EMA(dataframe['close'], timeperiod=12)
    dataframe['trend_close_2h'] = ta.EMA(dataframe['close'], timeperiod=24)
    dataframe['trend_close_4h'] = ta.EMA(dataframe['close'], timeperiod=48)
    dataframe['trend_close_6h'] = ta.EMA(dataframe['close'], timeperiod=72)
    dataframe['trend_close_8h'] = ta.EMA(dataframe['close'], timeperiod=96)
    
    # Open trend: EMA3, 6, 12, 24, 48, 72, 96
    dataframe['trend_open_5m'] = dataframe['open']
    dataframe['trend_open_15m'] = ta.EMA(dataframe['open'], timeperiod=3)
    dataframe['trend_open_30m'] = ta.EMA(dataframe['open'], timeperiod=6)
    dataframe['trend_open_1h'] = ta.EMA(dataframe['open'], timeperiod=12)
    dataframe['trend_open_2h'] = ta.EMA(dataframe['open'], timeperiod=24)
    dataframe['trend_open_4h'] = ta.EMA(dataframe['open'], timeperiod=48)
    dataframe['trend_open_6h'] = ta.EMA(dataframe['open'], timeperiod=72)
    dataframe['trend_open_8h'] = ta.EMA(dataframe['open'], timeperiod=96)

    dataframe['fan_magnitude'] = (dataframe['trend_close_1h'] / dataframe['trend_close_8h'])
    dataframe['fan_magnitude_gain'] = dataframe['fan_magnitude'] / dataframe['fan_magnitude'].shift(1)

    ichimoku = ftt.ichimoku(dataframe, conversion_line_period=20, base_line_periods=60, laggin_span=120, displacement=30)
    dataframe['chikou_span'] = ichimoku['chikou_span']
    dataframe['tenkan_sen'] = ichimoku['tenkan_sen']
    dataframe['kijun_sen'] = ichimoku['kijun_sen']
    dataframe['senkou_a'] = ichimoku['senkou_span_a']
    dataframe['senkou_b'] = ichimoku['senkou_span_b']
    dataframe['leading_senkou_span_a'] = ichimoku['leading_senkou_span_a']
    dataframe['leading_senkou_span_b'] = ichimoku['leading_senkou_span_b']
    dataframe['cloud_green'] = ichimoku['cloud_green']
    dataframe['cloud_red'] = ichimoku['cloud_red']

    dataframe['atr'] = ta.ATR(dataframe)

    return dataframe

In [74]:
ada_usdt_df = populate_indicators(ada_usdt)

Plotting

In [77]:
def plot_candlestick(df):
    fig = go.Figure(
        data=[go.Candlestick(x=df.index,
        open=df['open'],
        high=df['high'],
        low=df['low'],
        close=df['close'])]
    )
    fig.show()

In [78]:
plot_candlestick(ada_usdt_df)